# Folium

Testing ground for creating choropleths with our ward/FSA geojsons

In [1]:
import folium

In [3]:
m = folium.Map(location=[43.64448905083427, -79.3821119760047])
m

In [4]:
import requests

# Toronto Open Data is stored in a CKAN instance. It's APIs are documented here:
# https://docs.ckan.org/en/latest/api/

# To hit our API, you'll be making requests to:
base_url = "https://ckan0.cf.opendata.inter.prod-toronto.ca"

# Datasets are called "packages". Each package can contain many "resources"
# To retrieve the metadata for this package and its resources, use the package name in this page's URL:
url = base_url + "/api/3/action/package_show"
params = { "id": "city-wards"}
package = requests.get(url, params = params).json()

# To get resource data:
for idx, resource in enumerate(package["result"]["resources"]):

       # for datastore_active resources:
       if resource["datastore_active"]:

           # To get all records in CSV format:
           url = base_url + "/datastore/dump/" + resource["id"]
           resource_dump_data = requests.get(url).text
           print(resource_dump_data)

           # To selectively pull records and attribute-level metadata:
           url = base_url + "/api/3/action/datastore_search"
           p = { "id": resource["id"] }
           resource_search_data = requests.get(url, params = p).json()["result"]
           print(resource_search_data)
           # This API call has many parameters. They're documented here:
           # https://docs.ckan.org/en/latest/maintaining/datastore.html

       # To get metadata for non datastore_active resources:
       if not resource["datastore_active"]:
           url = base_url + "/api/3/action/resource_show?id=" + resource["id"]
           resource_metadata = requests.get(url).json()
           print(resource_metadata)
           # From here, you can use the "url" attribute to download this file


{'help': 'https://ckan0.cf.opendata.inter.prod-toronto.ca/api/3/action/help_show?name=resource_show', 'success': True, 'result': {'cache_last_updated': None, 'cache_url': None, 'created': '2019-07-23T16:47:44.729558', 'datastore_active': False, 'format': 'ZIP', 'hash': '', 'id': '35f67d86-cfc8-4483-8d77-50d035b010d9', 'is_datastore_cache_file': False, 'is_preview': False, 'last_modified': '2019-09-10T20:04:44.531748', 'metadata_modified': '2022-03-10T16:55:12.910726', 'mimetype': 'application/zip', 'mimetype_inner': None, 'name': '25-ward-model-december-2018-wgs84-latitude-longitude', 'package_id': '5e7a8234-f805-43ac-820f-03d7c360b588', 'position': 0, 'resource_type': None, 'revision_id': '989a1ec9-58c8-499d-8983-a7cd35ebc742', 'size': 282821, 'state': 'active', 'url': 'https://ckan0.cf.opendata.inter.prod-toronto.ca/dataset/5e7a8234-f805-43ac-820f-03d7c360b588/resource/35f67d86-cfc8-4483-8d77-50d035b010d9/download/25-ward-model-december-2018-wgs84-latitude-longitude.zip', 'url_type':

In [5]:
city_wards = "../data/city-wards-boundary.geojson"
folium.GeoJson(data=city_wards, name="geojson").add_to(m)
m

In [6]:
import pandas as pd

In [7]:
rentals = pd.read_csv('../data/notebooks/short-term-rental-registrations-data.csv')
rentals.dtypes

_id                               int64
operator_registration_number     object
postal_code                      object
ward_number                     float64
ward_name                        object
dtype: object

In [13]:
rental_count = rentals.groupby('ward_name').size()
rental_count

ward_name
Beaches-East York            277
Davenport                    413
Don Valley East               89
Don Valley North             153
Don Valley West              114
Eglinton-Lawrence            132
Etobicoke Centre             142
Etobicoke North               96
Etobicoke-Lakeshore          271
Humber River-Black Creek     107
Parkdale-High Park           317
Scarborough Centre            97
Scarborough North             56
Scarborough Southwest        170
Scarborough-Agincourt         91
Scarborough-Guildwood         86
Scarborough-Rouge Park        92
Spadina-Fort York           1810
Toronto Centre               595
Toronto-Danforth             356
Toronto-St. Paul's           215
University-Rosedale          511
Willowdale                   255
York Centre                  120
York South-Weston            155
dtype: int64

In [ ]:
folium.Choropleth(
    geo_data=city_wards,
    name='choropleth',
    data=rental_count,
    # columns=[''] # passing a series, so no need to specify columns
    key_on='feature.properties.AREA_NAME',
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Short term rentals",
).add_to(m)
folium.LayerControl().add_to(m)
m

The `key_on` feature refers to the variable in the geojson file for our `series` to bind to. Strangely, even though the json has `features`, the above only runs if I use `feature`. The [docs state that this argument *must start with `feature`*](https://python-visualization.github.io/folium/modules.html?highlight=choropleth#folium.features.Choropleth)